###### COVID-19: Comparisons


I am curious about COVID-19, and this notebook is my effort to find context and perspective from responsible, public data.

All data used is from:

- [The *New York Times*](https://github.com/nytimes/covid-19-data)
- [“Deaths and Mortality”, CDC](https://www.cdc.gov/nchs/fastats/deaths.htm)
- [“Stats of the State of South Carolina”, CDC](https://www.cdc.gov/nchs/pressroom/states/southcarolina/southcarolina.htm)
- [South Carolina Department of Health and Environmental Control (DHEC)](https://www.scdhec.gov/vital-records/parentage/sc-vital-records-data-and-statistics)
- [The Office of National Statistics, UK](https://www.ons.gov.uk/peoplepopulationandcommunity/birthsdeathsandmarriages/deaths/datasets/weeklyprovisionalfiguresondeathsregisteredinenglandandwales)
- [Civil Services State Governors Data](https://github.com/CivilServiceUSA/us-governors)
- [A map of the US cities and states under lockdown — and those that are reopening. Business Insider (updated as of May 28)](https://www.businessinsider.com/us-map-stay-at-home-orders-lockdowns-2020-3)
- [See Which States Are Reopening and Which Are Still Shut Down](https://www.nytimes.com/interactive/2020/us/states-reopen-map-coronavirus.html)
- [2016 United States Presidential Election. Wikipedia](https://en.wikipedia.org/wiki/2016_United_States_presidential_election)
- [States with the Fewest Coronavirus Restrictions](https://wallethub.com/edu/states-with-the-fewest-coronavirus-restrictions/73818/#expert=kelsey-hample)

The top part of this notebook consists of configurations. The more interesting stuff is below. I am not a professional any of the domains that this notebook touches on, so I make no claims.

Furthermore, I know that the data, even that from respectable sources, is all over the place, so any model, and especially amateur models like the present one, are pretty much guaranteed to be wrong. See [this very clear presentation](https://xkcd.com/2295/).

If there is any value here, it is in taking the same data that we see all over the place, and telling different stories with it.

## Days as of last update: 721

In [1]:
val handle = Markdown(s"""
## Days as of this update: [??]
""")


## Days as of this update: 721


## Configuring Libraries for the Almond Kernel

First, we'll make a bintray repository with libraries available to the almond kernel.

In [2]:
val myBT = coursierapi.MavenRepository.of("https://dl.bintray.com/neelsmith/maven")

interp.repositories() ++= Seq(myBT)

myBT: coursierapi.MavenRepository = MavenRepository(https://dl.bintray.com/neelsmith/maven)

Next, we bring in specific libraries from the new repository using almond's `$ivy` magic:

In [3]:
import $ivy.`org.plotly-scala::plotly-almond:0.7.1`
import plotly._, plotly.element._, plotly.layout._, plotly.Almond._

// if you want to have the plots available without an internet connection:
init(offline=true)

// restrict the output height to avoid scrolling in output cells
repl.pprinter() = repl.pprinter().copy(defaultHeight = 8)

import $ivy.$                                      

import plotly._, plotly.element._, plotly.layout._, plotly.Almond._

// if you want to have the plots available without an internet connection:


## Imports

From this point on, the notebook consists of completely generic Scala.

In [4]:
import almond.display.UpdatableDisplay
import almond.interpreter.api.DisplayData.ContentType
import almond.interpreter.api.{DisplayData, OutputHandler}

import java.io.File
import java.io.PrintWriter

import scala.io.Source

import java.text.SimpleDateFormat
import java.util.Date


import almond.display.UpdatableDisplay

import almond.interpreter.api.DisplayData.ContentType

import almond.interpreter.api.{DisplayData, OutputHandler}


import java.io.File

import java.io.PrintWriter


import scala.io.Source


import java.text.SimpleDateFormat

import java.util.Date


## Useful Functions

Pretty Print Things:

In [5]:
def showMe(v:Any):Unit = {
  v match {
    case _:Vector[Any] => println(s"""\n----\n${v.asInstanceOf[Vector[Any]].mkString("\n")}\n----\n""")
    case _:Iterable[Any] => println(s"""\n----\n${v.asInstanceOf[Iterable[Any]].mkString("\n")}\n----\n""")
    case _ => println(s"\n-----\n${v}\n----\n")
  }
}

defined function showMe

Validate an `Option[String]` as a valid date in 2020, or `None`.

In [6]:
def isValidDate( dOpt: Option[String]): Boolean = {
    
    val monthMap: Map[Int, Int] = {
        Map(1 -> 31,
        2 -> 29,
        3 -> 31,
        4 -> 30,
        5 -> 31,
        6 -> 30,
        7 -> 31,
        8 -> 31,
        9 -> 30,
        10 -> 31,
        11 -> 30,
        12 -> 31)
    }
    
    dOpt match {
        case Some(dateString) => {
            val y: Int = dateString.split("-")(0).toInt
            val m: Int = dateString.split("-")(1).toInt
            val d: Int = dateString.split("-")(2).toInt
            
            val goodYear = (y == 2020)
            val goodMonth = ( (1 to 12).contains(m) )
            val goodDay = {
                (d >= 1) &
                (d <= monthMap(m))
            }
            (goodYear & goodMonth & goodDay)
        }
        case None => true
    }
    
}

defined function isValidDate

## Load Some Data

Load up-to-date data from the NY Times. Source: <https://github.com/nytimes/covid-19-data>.

In [7]:
val dataLines: Vector[String] = {
    scala.io.Source.fromURL("https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv").mkString.split("\n").toVector.tail
}

// quick test
val badLines = dataLines.filter( l => {
    l.split(",").size != 5
})

assert ( badLines.size == 0 )


dataLines: Vector[String] = Vector(
  "2020-01-21,Washington,53,1,0",
  "2020-01-22,Washington,53,1,0",
  "2020-01-23,Washington,53,1,0",
  "2020-01-24,Illinois,17,1,0",
  "2020-01-24,Washington,53,1,0",
  "2020-01-25,California,06,1,0",
...
badLines: Vector[String] = Vector()

Let's make an indexed Vector of dates… it will be easier to work with later…

In [8]:
val listOfDates1: Vector[String] = dataLines.map(_.split(",").head).toVector.distinct

val listOfDates2: Vector[String] = Vector()

val listOfDates = (listOfDates1 ++ listOfDates2).distinct

// showMe(listOfDates)

listOfDates1: Vector[String] = Vector(
  "2020-01-21",
  "2020-01-22",
  "2020-01-23",
  "2020-01-24",
  "2020-01-25",
  "2020-01-26",
...
listOfDates2: Vector[String] = Vector()
listOfDates: Vector[String] = Vector(
  "2020-01-21",
  "2020-01-22",
  "2020-01-23",
  "2020-01-24",
  "2020-01-25",
  "2020-01-26",
...

A separate data-file, `politics_and_lockdown.csv`, to be merged with our day-by-day report from the NYT.

We'll make a class, `StateStat`, to organize this data. We'll save a `StateStat` for each state in `stateStats: Vector[StateStat]`.

That file's field-headings are:

~~~
state,population,politics,total-lockdown,partial-lockdown,opening
~~~

In [9]:
case class StateStat( 
    state:String, 
    population: Int, 
    isRedState: Boolean,
    partialLock: Option[String], 
    totalLock: Option[String],
    open: Option[String]
)

val stateStats: Map[String, StateStat] = {
    val fileName = "politics_and_lockdown_pres.csv"
    scala.io.Source.fromFile(fileName).mkString.split("\n").toVector.tail.map( l => {
        val state: String = l.split(",").toVector(0)
        val population: Int = l.split(",").toVector(1).toInt
        val isRedState: Boolean = l.split(",").toVector(2).trim match {
            case "republican" => true
            case _ => false
        }
        val partialLock = l.split(",").toVector(4) match {
            case "none" => None
            case _ => Some(l.split(",").toVector(4))
        }
        val totalLock = l.split(",").toVector(3) match {
            case "none" => None
            case _ => Some(l.split(",").toVector(3))
        }
        val open = l.split(",").toVector(5) match {
            case "none" => None
            case _ => Some(l.split(",").toVector(5))
        }
        (state, StateStat(state, population, isRedState, partialLock, totalLock, open))
    }).toMap
}

// Let's do a little sanity-checking on the dates…


val invalidDates: Vector[StateStat] = {
    stateStats.toVector.filter( ss => {
        val p: Option[String] = ss._2.partialLock
        val t: Option[String] = ss._2.totalLock
        val o: Option[String] = ss._2.open
        
        val bp: Boolean = isValidDate(p)
        val bt: Boolean = isValidDate(t)
        val bo: Boolean = isValidDate(o)
        
        val pInList: Boolean = {
            p match {
                case Some(s) => listOfDates.contains(s)
                case None => true
            }
        }
        val tInList: Boolean = {
            t match {
                case Some(s) => listOfDates.contains(s)
                case None => true
            }
        }
        val oInList: Boolean = {
            o match {
                case Some(s) => listOfDates.contains(s)
                case None => true
            }
        }
        
        val isInList: Boolean = (pInList & tInList & oInList)
        
        ((bp & bt & bo & isInList) == false)
    }).map(_._2)
}

if (invalidDates.size > 0) showMe(invalidDates)

assert( invalidDates.size == 0)

defined class StateStat
stateStats: Map[String, StateStat] = Map(
  "New Mexico" -> StateStat(
    "New Mexico",
    2096829,
    false,
    Some("2020-05-16"),
    Some("2020-03-24"),
...
invalidDates: Vector[StateStat] = Vector()

## Make Data Structures

For each day reported for each state, we want the following information:

- Date
- State
- State population (based on 2018 data)
- Red state? (a `boolean`). Based on party of the governor, with two exceptions described below
- New Deaths
- New Cases
- Total Deaths by this day
- Total Cases by this day
- Lockdown state on this date (based on [this article](https://www.nytimes.com/interactive/2020/us/states-reopen-map-coronavirus.html))
    - `0` = no lockdown, or lockdown lifted
    - `1` = partial state lockdown
    - `2` = state lockdown
    
States reported their first cases on different dates, of course, so we'll need to pad the data on the left so they all start on the same day (January 21, 2020, when Washington reported its first case).

Since “open”, “closed”, “locked-down”, *etc.* are vague terms, I am calling any state with a “Stay at Home” order to be fully closed, and any state that allows indoor restaurant dining to be fully open, as these things go.

### A Note on Red vs. Blue

The file `politics_and_lockdown.csv` in this repository lists states, with their 2018 populations, and their political leaning. The latter category is of course slippery. I based this version on (1) how the state voted in the 2016 presidential election, but also (2) the political party of the governor. I used my own, fallible, subjective judgement about which category to use, when (1) and (2) disagreed. So, Massachusetts was very, very blue in 2016, and I left it that way despite the state's having a Republican governor. On the other hand, Michigan was a red-state in 2016, but its Democratic governor seems to be playing a very dominant role in that state's response to the crisis, so Michigan is "blue" in this chart.

**If you disagree, please edit the file `politics_and_lockdown.csv`, and re-run the scripts to see what you see!**


In [10]:
case class StateDay(
    date: String,
    state: String,
    population: Int,
    isRedState: Boolean,
    newDeaths: Int,
    newCases: Int,
    totalDeaths: Int,
    totalCases: Int,
    activeCases: Int,
    lockdown: Int
)

defined class StateDay

First, let's split out our raw data so each state's data is in a Vector[String]. We'll make a Vector of those: `Vector[Vector[String]]`. This will let us do the initial normalization (padding left so they all start on `2020-01-21').

We can do some consistency-checking while we're at it.

In [11]:
// For each state, a vector of that state's daily records, from the NYTimes
val dataVec1: Vector[Vector[String]] = { 
    // get just the states
    val justStates: Vector[String] = dataLines.map( dl => {
        dl.split(",")(1)
    })
    // map dataLines to states
    val zippedWithState: Vector[(String, String)] = justStates.zip(dataLines)
    // group by state
    val interim1: Vector[(String, Vector[(String, String)])] = {
        zippedWithState.groupBy(_._1).toVector
    }
    // simplify
    val interim2: Vector[Vector[String]] = interim1.map( i1 => {
        (i1._1, i1._2.map(_._2))
    }).map(_._2)
    // sort, first by date within state, then by number of days
    interim2.map( i2 => {
        i2.sortBy(_.split(",")(0))
    }).sortBy(_.size)
}

// Let's filter out everything but the 50 states and DC…
val justThe50: Vector[Vector[String]] = dataVec1.filter( dv => {
    val fiftyStates: Vector[String] = stateStats.keys.toVector
    fiftyStates.contains(dv.head.split(",")(1))
})



dataVec1: Vector[Vector[String]] = Vector(
  Vector(
    "2021-09-22,American Samoa,60,1,0",
    "2021-09-23,American Samoa,60,1,0",
    "2021-09-24,American Samoa,60,1,0",
    "2021-09-25,American Samoa,60,1,0",
    "2021-09-26,American Samoa,60,1,0",
...
justThe50: Vector[Vector[String]] = Vector(
  Vector(
    "2020-03-17,West Virginia,54,1,0",
    "2020-03-18,West Virginia,54,2,0",
    "2020-03-19,West Virginia,54,5,0",
    "2020-03-20,West Virginia,54,8,0",
    "2020-03-21,West Virginia,54,12,0",
...

## Build the Real Data

For reference:

~~~
case class StateStat( 
    state:String, 
    population: Int, 
    isRedState: Boolean,
    partialLock: Option[String], 
    totalLock: Option[String],
    open: Option[String]
)
~~~

And what we want is a Vector[Vector[StateDay]]:

~~~
case class StateDay(
    date: String,
    state: String,
    population: Int,
    isRedState: Boolean,
    newDeaths: Int,
    newCases: Int,
    totalDeaths: Int,
    totalCases: Int,
    activeCases: Int,
    lockdown: Int
)
~~~

We start by mapping `justThe50` (above) to a Vector[Vector[StateDay]], which will require some helper-fnctions, and merging it with `stateStats`.

Because calculating the lockdown data for a given day is a little fiddly, let's make a first-cut, getting everything into a good data-structure, easier to work with than a delimited String, then go back and sort out lockdown data. 

In [12]:
def oneStateVector( stats: Map[String, StateStat] = stateStats, sv: Vector[String]): Vector[StateDay] = {
    
    // Make sure we've sorted by date
                                       
    val sortedSv = sv.sortBy( d => {
        d.split(",")(0)
    })                           
                                       
    sortedSv.zipWithIndex
            .map( recString => {
                val fields: Vector[String] = recString._1.split(",").toVector
                val date: String = fields(0)
                val state: String = fields(1)
                val totalCases: Int = fields(3).toInt // NYT gives a running toll
                val totalDeaths: Int = fields(4).toInt // NYT gives a running toll
                
                val i = recString._2
                
                // By subtraction from the previous totalCases, get newCases
                val newCases: Int = {
                    if (i == 0) totalCases
                    else {
                        val totalToday: Int = totalCases
                        val totalPrev: Int = {
                            sortedSv(i-1).split(",")(3).toInt
                        }
                        totalToday - totalPrev
                    }
                }
                
                // By subtraction from the previous totalDeaths, get newDeaths
                val newDeaths: Int = {
                    if (i == 0) totalDeaths
                    else {
                        val totalToday: Int = totalDeaths
                        val totalPrev: Int = {
                            sortedSv(i-1).split(",")(4).toInt
                        }
                        totalToday - totalPrev
                    }
                }
                
                // Get the easy stuff from stats…
                val population: Int = stats(state).population
                val isRedState: Boolean = stats(state).isRedState
                
                // Get today's lockdown state!
                val lockdown: Int = 0
                
                // We'll fill in activeCases later!
                val activeCases: Int = 0
                
                StateDay( date,
                         state,
                         population,
                         isRedState,
                         newDeaths,
                         newCases,
                         totalDeaths,
                         totalCases,
                         activeCases,
                         lockdown
                        )
            })
}

val dailyStateRecords_invalidLockdownData: Vector[Vector[StateDay]] = {
    justThe50.map( s => {
        oneStateVector( stateStats, s)
    })
}



defined function oneStateVector
dailyStateRecords_invalidLockdownData: Vector[Vector[StateDay]] = Vector(
  Vector(
    StateDay("2020-03-17", "West Virginia", 1792147, true, 0, 1, 0, 1, 0, 0),
    StateDay("2020-03-18", "West Virginia", 1792147, true, 0, 1, 0, 2, 0, 0),
    StateDay("2020-03-19", "West Virginia", 1792147, true, 0, 3, 0, 5, 0, 0),
    StateDay("2020-03-20", "West Virginia", 1792147, true, 0, 3, 0, 8, 0, 0),
    StateDay("2020-03-21", "West Virginia", 1792147, true, 0, 4, 0, 12, 0, 0),
...

## Padding the Days

Different states started reporting on different dates. We need all of our states Vectors of `StateDay` objects to be the same length, so we need to pad them with "empty" records on the "left". We find the state that has the longest reporting record (Washington, but we'll find it programmatically), and use its records as the default length. We'll padd all the others to match.

As we do this, remember:

~~~
case class StateDay(
    date: String,
    state: String,
    population: Int,
    isRedState: Boolean,
    newDeaths: Int,
    newCases: Int,
    totalDeaths: Int,
    totalCases: Int,
    activeCases: Int,
    lockdown: Int
)
~~~

We will use `listOfDates`, a `Vector[String]` defined above, and a representative `StateDay` to give us the data we need.

In [13]:
def blankDayVec( howMany: Int, state: StateDay ): Vector[StateDay] = {
    val dateVec: Vector[String] = listOfDates.toVector.take(howMany)
    dateVec.map( date => {
        StateDay(
            date,
            state.state,
            state.population,
            state.isRedState,
            0,0,0,0,0,0
        )
    })
}

// Sort the states by number of days, take the size of the biggest
val maxRecords: Int = dailyStateRecords_invalidLockdownData.sortBy(_.size).last.size

val dailyStateRecords_normalized: Vector[Vector[StateDay]] = {
    dailyStateRecords_invalidLockdownData.map( stateVec => {
        val size: Int = stateVec.size
        val diff: Int = maxRecords - size
        if (diff == 0) stateVec
        else {
            val paddingVec: Vector[StateDay] = {
                blankDayVec( diff, stateVec.head )
            }
            paddingVec ++ stateVec
        }
    })
}

// Check that it worked! 

assert ( dailyStateRecords_normalized.map(_.size).distinct.size == 1 )

// Un-comment the line below to see the result
//for ( s <- dailyStateRecords_normalized)  showMe(s)


defined function blankDayVec
maxRecords: Int = 721
dailyStateRecords_normalized: Vector[Vector[StateDay]] = Vector(
  Vector(
    StateDay("2020-01-21", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-22", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-23", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-24", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-25", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
...

In [14]:
handle.withContent(s"""
## Days as of this update: ${maxRecords}
""").update()

Now we can take `dailyStateRecords_invalidLockdownData` and map it to another `Vector[Vector[StateDay]]` with valid data for the lockdown state on each day. We will use `listOfDates`, a `Vector[String]` defined above.

We'll start with a Class `LockdownEvent`, which will have to parameters: a day-index, and a lockdown state (0,1,2) as described above: 0 = no lockdown or full open, 1 = partial lockdown, 2 = full lockdown.

In [15]:
case class LockdownEvent( dayIndex: Int, lockdownState: Int )

def getLockdownState( 
    record: StateDay, 
    stateRecords: Vector[StateDay], 
    stats: Map[String, StateStat] = stateStats): Int = {
    
    val i: Int = stateRecords.indexOf(record)
    
    // every state started at lockdown = 0
    if (i == 0) { 0 }
    /* 
        otherwise, we get the date of partial-lockdown, total-lockdown, and opening
        and see which was the most recent previous event.
    */
    else {
        val sstat: StateStat = stats(record.state)
        val partLock: Option[String] = sstat.partialLock
        val totalLock: Option[String] = sstat.totalLock
        val open: Option[String] = sstat.open
             
        /*
        Now we get the dateIndex for this record
        */
        
        val todayIndex: Int = listOfDates.indexOf(record.date)
        //println(s"${record.state} :: ${i} :: ${todayIndex}")
        
        /*
        For each event (lockdown states 0,1,2, see above), let's make a LockdownEvent object.
        If an event is None, we put it at Day 0.
        */
        
        val partLockEvent: LockdownEvent = {
            partLock match {
                case Some(d) => {
                    val dayIndex: Int = listOfDates.indexOf(d)
                    LockdownEvent(dayIndex, 1)
                }
                case None => LockdownEvent(0, 0)
            }
        }
        val totalLockEvent: LockdownEvent = {
            totalLock match {
                case Some(d) => {
                    val dayIndex: Int = listOfDates.indexOf(d)
                    LockdownEvent(dayIndex, 2)
                }
                case None => LockdownEvent(0, 0)
            }
        }
        val openEvent: LockdownEvent = {
            open match {
                case Some(d) => {
                    val dayIndex: Int = listOfDates.indexOf(d)
                    LockdownEvent(dayIndex, 0)
                }
                case None => LockdownEvent(0, 0)
            }
        }
      //println(s"${totalLockEvent} :: ${partLockEvent} :: ${openEvent}")
     
        // We make a Vector of these, filter for earler ones, and take the last.
        val eventVec: Vector[LockdownEvent] = {
            Vector( partLockEvent, totalLockEvent, openEvent ).sortBy( e => {
                e.dayIndex
            })
        }
        
        //for ( e <- eventVec) println( e )
        
       // showMe(todayIndex)
       // showMe(eventVec)
        
        val mostRecent: LockdownEvent = {
            val validEvents: Vector[LockdownEvent] = eventVec.filter( _.dayIndex <= todayIndex)
            if (validEvents.size > 0) validEvents.last
            else LockdownEvent(todayIndex, 0)
        }
        
        //println(s"${record.state} :: ${todayIndex} :: ${mostRecent.lockdownState}")
            
        // return the lockdown State
        mostRecent.lockdownState
        
    }
}



defined class LockdownEvent
defined function getLockdownState

And we'll sort by State-name while we're at it

In [16]:
val dailyStateRecords_unsorted: Vector[Vector[StateDay]] = {
    dailyStateRecords_normalized.map( vsd => {
        vsd.map( record => {
            val lockdownState: Int = getLockdownState( record, vsd )
            StateDay( record.date,
                     record.state,
                     record.population,
                     record.isRedState,
                     record.newDeaths,
                     record.newCases,
                     record.totalDeaths,
                     record.totalCases,
                     record.activeCases,
                     lockdownState
                    )
        })
    })
}


dailyStateRecords_unsorted: Vector[Vector[StateDay]] = Vector(
  Vector(
    StateDay("2020-01-21", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-22", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-23", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-24", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-25", "West Virginia", 1792147, true, 0, 0, 0, 0, 0, 0),
...

In [17]:
val dailyStateRecords_sorted: Vector[Vector[StateDay]] = dailyStateRecords_unsorted.sortBy(_.head.state)

// Un-comment the line below to see the data…
//for ( s <- dailyStateRecords_sorted)  showMe(s)


dailyStateRecords_sorted: Vector[Vector[StateDay]] = Vector(
  Vector(
    StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-24", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-25", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...

## Calculate Active Cases

If you have been paying attention, you will have seen that we punted on "active cases". No one reports these consistently, so we'll have to calculate them for each State's daily data. In other words, we'll make something up.

But we couldn't make something up until we had a normalized dataset, with the same number of days for each state, so we've saved this for last.

We can assume that there is some **n**, where **n = days-until-death-or-recovery**. I am not a physician or epidemiologist, so I'll just have to make up a number.

That number is defined below, as `activeCaseThreshold`. It is an `Int` representing a number of days. 

The way it will work is this: Any reported case that is farther in the past than **n-days** will be considered *inactive*. The difference between the current *total cases* and these calculated *inactive cases* will be the **active cases**.

**You can change it, and change the results!**

In [18]:
val activeCaseThreshold: Int = 14

activeCaseThreshold: Int = 14

So let's make one final version of our `Vector[Vector[StateDay]]` with calculated active cases.

In [19]:
val stateRecords: Vector[Vector[StateDay]] = {

    dailyStateRecords_sorted.map ( vsdd => {

        vsdd.zipWithIndex.map( isd => {
            val i: Int = isd._2
            val record: StateDay = isd._1

            val activeCases: Int = {
                if (i <= activeCaseThreshold) record.totalCases
                else {
                    val inactive = vsdd(i - activeCaseThreshold).totalCases
                    record.totalCases - inactive
                }
            }

            StateDay( record.date,
                     record.state,
                     record.population,
                     record.isRedState,
                     record.newDeaths,
                     record.newCases,
                     record.totalDeaths,
                     record.totalCases,
                     activeCases,
                     record.lockdown
                    )


        })

    })
}

// Un-comment the line below to see the result
//for ( s <- dailyStateRecords)  showMe(s)


stateRecords: Vector[Vector[StateDay]] = Vector(
  Vector(
    StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-24", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
    StateDay("2020-01-25", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...

## A More Clear Data Structure

A `Vector[Vector[StateDay]]` is going to get confusing, so let's make a Class with better names.

What we have is an outer Vector containg data for states. For each state, we have a `Vector[StateDay]`; we will call this `OneStateData`. 

A `Vector[OneStateData]` will be `statesData`, our list of data for the 50 states plus DC.

While we're at it, we can make a function `getAState( state: String )` that filters `statesData` for data from a single state.

In [20]:
case class OneStateData( days: Vector[StateDay]) 

case class StatesData( states: Vector[OneStateData] )

val statesData: StatesData = {
    val allStates: Vector[OneStateData] = stateRecords.map( ss => {
        OneStateData( ss )
    })
    StatesData( allStates )
}

def getAState( state: String, data: Vector[OneStateData] = statesData.states): OneStateData = {
    val sr: Vector[OneStateData] = data.filter(_.days.head.state == state)
    sr.head
}

//showMe(getAState("Utah").days)

defined class OneStateData
defined class StatesData
statesData: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...
defined function getAState

## Ready to Work

At this point, we have a "list of lists" in the form of `statesData`. The top-level list is the 50 states plus the District of Columbia. We will test this.

For each state, we have a list of daily reports, each report showing:

~~~
case class StateDay(
    date: String,
    state: String,
    population: Int,
    isRedState: Boolean,
    newDeaths: Int,
    newCases: Int,
    totalDeaths: Int,
    totalCases: Int,
    activeCases: Int,
    lockdown: Int
)
~~~



In [21]:
// last tests

// There should be 51
assert( statesData.states.size == 51 )

// They should all be the same size
assert( statesData.states.map(_.days.size).distinct.size == 1)


# Questions


Now that we've spent hundreds of lines of code sorting things out, we can ask questions:

- Which states have been the most, and which the least, "locked down"? (This should require undoing the normalization we did above, since it isn't fair to give states credit or blame for being "not locked down" before they had any cases.)
- How does that map to politics?
- How does degree of lockdown map to cases and deaths?

(Please read, above, where I describe my subjective mapping of states to "red" or "blue". You can edit my state mapping to get other views.)


### Degree of Lockdown

We want to take each state's data, truncate it on the left with the first reported case, and average its lockdown-degree, as an average of "lockdown state per day". We'll multiply by 100 so we can work with 3 significant figures while still doing integer arithmetic. States that never locked down at all will have an average of 0 (see Nebraska, for example). If a hypothetical state fully locked down upon reporting of the first case, it would have an average of 200 (Delaware comes closest, as of 5/12/2020).

In [22]:
def oneStateLockdownScore( state: String, report: Boolean = true): Int = {
    val stateRecords: OneStateData = statesData.states.filter(_.days.head.state == state).head
    if (report) println(s"\n-----\n${state}")
    val stateFirstCaseRecord = stateRecords.days.find( _.newCases > 0 ).get
    val stateFirstCaseRecordIndex = stateRecords.days.indexOf(stateFirstCaseRecord)
    val stateRecordsClipped = stateRecords.days.takeRight(stateRecords.days.size - stateFirstCaseRecordIndex).filter(_.state == state) 
    //showMe(stateRecordsClipped)
    if (report) println(s"Days since first case: ${stateRecordsClipped.size}")
    val stateLDScores = stateRecordsClipped.map( _.lockdown * 100 )
    //println(s"State LD Scores: ${state}")
    //showMe(stateLDScores)
    val stateClippedSize = stateRecordsClipped.size
    val stateLDAverage = stateLDScores.sum / stateClippedSize
    if (report) println(s"${stateLDScores.sum} /  ${stateRecordsClipped.size} = ${stateLDAverage}\n-----")
    
    stateLDAverage
}

val stateScores: Vector[(String, Int)] = statesData.states.map( dsr => {
    val state: String = dsr.days.head.state
    (state, oneStateLockdownScore(state, false))
}).sortBy(_._2)

//Un-comment the code block below to list states by degree of lockdown

println("============================================\nStates Ranked By Lockdown: Greatest to Least\n")
for (ss <- stateScores.reverse.zipWithIndex) {
    val rank = ss._2 + 1
    val state = ss._1._1
    val score = ss._1._2
    println(s"${rank}. ${state} ${score}")
}


States Ranked By Lockdown: Greatest to Least

1. Wisconsin 99
2. District of Columbia 28
3. New Jersey 26
4. New York 24
5. Delaware 23
6. Connecticut 23
7. Oregon 22
8. Massachusetts 22
9. California 21
10. Washington 20
11. Michigan 20
12. Maryland 20
13. Rhode Island 19
14. Illinois 19
15. Vermont 18
16. New Mexico 18
17. Minnesota 18
18. Virginia 17
19. Ohio 17
20. Maine 17
21. Louisiana 17
22. Hawaii 17
23. Pennsylvania 15
24. Oklahoma 15
25. New Hampshire 15
26. Kentucky 15
27. West Virginia 14
28. North Carolina 13
29. Mississippi 13
30. Indiana 13
31. Kansas 12
32. Alaska 12
33. Nevada 11
34. Florida 11
35. Montana 10
36. Idaho 10
37. Colorado 10
38. Tennessee 9
39. Alabama 9
40. Texas 8
41. Missouri 8
42. Iowa 8
43. Georgia 6
44. South Carolina 5
45. Arkansas 5
46. Arizona 5
47. North Dakota 4
48. Utah 2
49. Wyoming 1
50. South Dakota 0
51. Nebraska 0


defined function oneStateLockdownScore
stateScores: Vector[(String, Int)] = Vector(
  ("Nebraska", 0),
  ("South Dakota", 0),
  ("Wyoming", 1),
  ("Utah", 2),
  ("North Dakota", 4),
  ("Arizona", 5),
...

## Generally Useful Functions

Our basic data structure is a **list of lists of `StateDay` objects**. We might want to slice and dice this in various ways: "red" states vs. "blue" states, states at various degrees of lockdown, comparing particular states, etc.

All of this we can do with filtering our **list of lists**.

Let's make some functions that will take a `StatesData` and do some generically useful things to it.

In [23]:
val perCapitaNumber: Int = 1000000 // You can change this!

val formatter = java.text.NumberFormat.getIntegerInstance
val perCapString = formatter.format(perCapitaNumber)

def mountingDeaths( sd: StatesData, perCapita: Boolean = false, perCapAdj: Double = 1.0 ): Vector[Double] = {
    if (perCapita) {
         val population: Int = sd.states.map( _.days.head.population ).sum
         (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            val sumDeaths: Int = sd.states.map( state => {
                state.days(dayIndex).totalDeaths
            }).sum 
            (sumDeaths.toDouble * perCapitaNumber.toDouble) / population.toDouble
        })
    } else {
        (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            sd.states.map( state => {
                state.days(dayIndex).totalDeaths
            }).sum.toDouble
        })
    }
}

def dailyDeaths( sd: StatesData, perCapita: Boolean = false, perCapAdj: Double = 1.0 ): Vector[Double] = {
    if (perCapita) {
         val population: Int = sd.states.map( _.days.head.population ).sum
         (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            val sumDeaths: Int = sd.states.map( state => {
                state.days(dayIndex).newDeaths
            }).sum 
            (sumDeaths.toDouble * perCapitaNumber.toDouble) / population.toDouble
        })
    } else {
        (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            sd.states.map( state => {
                state.days(dayIndex).newDeaths
            }).sum.toDouble
        })
    }
}

def mountingCases( sd: StatesData, perCapita: Boolean = false, perCapAdj: Double = 1.0 ): Vector[Double] = {
    if (perCapita) {
         val population: Int = sd.states.map( _.days.head.population ).sum
         (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            val sumCases: Int = sd.states.map( state => {
                state.days(dayIndex).totalCases
            }).sum 
            (sumCases.toDouble * perCapitaNumber.toDouble) / population.toDouble
        })
    } else {
        (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            sd.states.map( state => {
                state.days(dayIndex).totalCases
            }).sum.toDouble
        })
    }
}

def dailyCases( sd: StatesData, perCapita: Boolean = false, perCapAdj: Double = 1.0 ): Vector[Double] = {
    if (perCapita) {
         val population: Int = sd.states.map( _.days.head.population ).sum
         (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            val sumCases: Int = sd.states.map( state => {
                state.days(dayIndex).newCases
            }).sum 
            (sumCases.toDouble * perCapitaNumber.toDouble) / population.toDouble
        })
    } else {
        (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            sd.states.map( state => {
                state.days(dayIndex).newCases
            }).sum.toDouble
        })
    }
}

def activeCases( sd: StatesData, perCapita: Boolean = false, perCapAdj: Double = 1.0 ): Vector[Double] = {
    if (perCapita) {
         val population: Int = sd.states.map( _.days.head.population ).sum
         (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            val sumCases: Int = sd.states.map( state => {
                state.days(dayIndex).activeCases
            }).sum 
            (sumCases.toDouble * perCapitaNumber.toDouble) / population.toDouble
        })
    } else {
        (0 until sd.states.head.days.size).toVector.map( dayIndex => {
            sd.states.map( state => {
                state.days(dayIndex).activeCases
            }).sum.toDouble
        })
    }
}

// Functions for centering curves

def centerCurves( curves: Vector[Vector[Double]]): Vector[Vector[Double]] = {
    case class CurveInfo( center: Double, leftSize: Int, rightSize: Int, totalLength: Int)
    
    val infos: Vector[CurveInfo] = curves.map( c => {
        val center: Double = c.max
        val centerIndex: Int = c.indexOf(center)
        val leftSize = centerIndex
        val rightSize = c.size - centerIndex - 1
        val tl = leftSize + rightSize + 1
        CurveInfo(center, leftSize, rightSize, tl)
    })
        
    val longestOnLeft: Int = {
        infos.map(_.leftSize).max
    }
        
    val longestOnRight: Int = {
        infos.map(_.rightSize).max
    }

    curves.zipWithIndex.map( ci => {
        val c = ci._1
        val i = ci._2
        val thisInfo: CurveInfo = infos(i)
        
        val paddingLeft: Vector[Double] = Vector.fill(longestOnLeft- thisInfo.leftSize )(0.0)
        val paddingRight: Vector[Double] = Vector.fill(longestOnRight - thisInfo.rightSize)(0.0)
        
        paddingLeft ++ c ++ paddingRight
    })
    
}




perCapitaNumber: Int = 1000000
formatter: java.text.NumberFormat = java.text.DecimalFormat@674dc
perCapString: String = "1,000,000"
defined function mountingDeaths
defined function dailyDeaths
defined function mountingCases
defined function dailyCases
defined function activeCases
defined function centerCurves

## Categories

We can do Red States vs. Blue States, groups by degree of lockdown, or individual states.

In [24]:
val redStates: StatesData = {
    val states: Vector[OneStateData] = statesData.states.filter(_.days.head.isRedState == true)
    StatesData(states)
}

val blueStates: StatesData = {
    val states: Vector[OneStateData] = statesData.states.filter(_.days.head.isRedState == false)
    StatesData(states)
}

// uncomment the lines below to see how the states divide up
println("=========\nBlue States\n=========")
for (s <- blueStates.states ) println(s.days.head.state )
println("\n=========\nRed States\n=========")
for (s <- redStates.states ) println(s.days.head.state )


val lockdownThirds: Map[String, StatesData] = {
    val howMany: Int = stateScores.size / 3
    val statesRanked: Vector[String] = stateScores.map(_._1)
    val lowStates: StatesData = {
        val chosenStates: Vector[OneStateData] = {
            val stateList: Vector[String] = statesRanked.take(howMany)
            statesData.states.filter( s => {
                stateList.contains(s.days.head.state)
            })
        }
        StatesData(chosenStates)
    }
    
    val middleStates: StatesData = {
        val chosenStates: Vector[OneStateData] = {
            val stateList: Vector[String] = statesRanked.takeRight(howMany * 2).take(howMany)
            statesData.states.filter( s => {
                stateList.contains(s.days.head.state)
            })
        }
        StatesData(chosenStates)
    }
    
    val highStates: StatesData = {
        val chosenStates: Vector[OneStateData] = {
            val stateList: Vector[String] = statesRanked.takeRight(howMany)
            statesData.states.filter( s => {
                stateList.contains(s.days.head.state)
            })
        }
        StatesData(chosenStates)
    }
    
    Map("low" -> lowStates, "middle" -> middleStates, "high" -> highStates)
}

def pickAState( state: String ): StatesData = {
    val states: Vector[OneStateData] = statesData.states.filter(_.days.head.state == state)
    StatesData(states)
}



Blue States
California
Colorado
Connecticut
Delaware
District of Columbia
Hawaii
Illinois
Louisiana
Maryland
Massachusetts
Michigan
Minnesota
Nevada
New Hampshire
New Jersey
New Mexico
New York
North Carolina
Oregon
Pennsylvania
Rhode Island
Vermont
Virginia
Washington
Wisconsin

Red States
Alabama
Alaska
Arizona
Arkansas
Florida
Georgia
Idaho
Indiana
Iowa
Kansas
Kentucky
Maine
Mississippi
Missouri
Montana
Nebraska
North Dakota
Ohio
Oklahoma
South Carolina
South Dakota
Tennessee
Texas
Utah
West Virginia
Wyoming


redStates: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...
blueStates: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay("2020-01-21", "California", 39512223, false, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-22", "California", 39512223, false, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-23", "California", 39512223, false, 0, 0, 0, 0, 0, 0),
...
lockdownThirds: Map[String, StatesData] = Map(
  "low" -> StatesData(
    Vector(
      OneStateData(
        Vector(
          StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
          StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...
defined function pickAState

### Graph Things

Let's write a parameterized function for graphing a `Vector[Vector[Int]]`, so we can throw at it any combination of lists and see what we can see. We'll want to parameterized "title" as well as a `Vector[String]` that are labels for each of our data vectors.


In [25]:

def getScatterVec( data: Vector[Vector[Double]], lables: Vector[String], color: Option[(Int, Int, Int, Double)] = None): Vector[Scatter] = {
    data.zipWithIndex.map( vi => {
        
        val colorList: Vector[(Int, Int, Int, Double)] = {
            Vector((240,0,0,1.0),(0,0,240,1.0),(0,240,0,1.0),(2,63,165,1.0),(125,135,185,1.0),(190,193,212,1.0),(214,188,192,1.0),(187,119,132,1.0),(142,6,59,1.0),(74,111,227,1.0),(133,149,225,1.0),(181,187,227,1.0),(230,175,185,1.0),(224,123,145,1.0),(211,63,106,1.0),(17,198,56,1.0),(141,213,147,1.0),(198,222,199,1.0),(234,211,198,1.0),(240,185,141,1.0),(239,151,8,1.0),(15,207,192,1.0),(156,222,214,1.0),(213,234,231,1.0),(243,225,235,1.0),(246,196,225,1.0),(247,156,212,1.0))
        }
        
        val index = vi._2
        val dataVec = vi._1
        val label = lables(index)
        val thisColor = {
            color match {
                case Some(tp) => tp
                case None => colorList( index % colorList.size )
            }
        }
    
        Scatter(
          (1 to dataVec.size),
          dataVec,
          name = label,
          mode = ScatterMode(ScatterMode.Lines),
          marker = Marker(
            color = Color.RGBA(
            thisColor._1,
            thisColor._2,
            thisColor._3,
            thisColor._4
           ),
          )
        )    
    })
}

def plotData( data: Vector[Vector[Double]], labels: Vector[String], title: String ): Unit = {
    
    val dataNew = getScatterVec( data, labels)
    val layoutNew = Layout(title)

    plot(dataNew, layoutNew)
}



defined function getScatterVec
defined function plotData

# Visualizations!

Finally, after all this setup, we can do some actual visualizations!

case class OneStateData( days: Vector[StateDay]) 

case class StatesData( states: Vector[OneStateData] )

val statesData: StatesData = {
    val allStates: Vector[OneStateData] = stateRecords.map( ss => {
        OneStateData( ss )
    })
    StatesData( allStates )
}

def getAState( state: String, data: Vector[OneStateData] = statesData.states): OneStateData = {
    val sr: Vector[OneStateData] = data.filter(_.days.head.state == state)
    sr.head
}



## Compare Selected States

Name some states to compare. Edit the code below. It should be obvious how.

In [26]:


val nDays: Int = 28

val pickFourStates: Vector[String] = {
    
  Vector(
      "Massachusetts", "Florida", "South Carolina"
  )
    //Vector("Delaware")
    
    
    /*Vector(
        "Illinois", "Louisiana", "Michigan", "Mississippi", "North Dakota", "South Dakota"
    )*/
    
    
    /*Vector(
        "South Carolina",
        "Michigan",
        "South Dakota"
       
    )*/
    
}


def toTrendLine( v: Vector[Double]): Vector[Double] = {
    case class XY( x: Double, y: Double)
    val xyVec: Vector[XY] = v.zipWithIndex.map( xy => XY(xy._2, xy._1))
    val n: Int = xyVec.size
    
    // `a` = n times the summation of all x-values multiplied by their corresponding y-values
    val a: Double = n * xyVec.map( xy => {
        xy.x * xy.y
    }).sum
    
    // `b` = the sum of all x-values times the sum of all y-values
    val b: Double = {
        xyVec.map(_.x).sum * xyVec.map(_.y).sum
    }
    
    //  `c` = n times the sum of all squared x-values
    val c: Double = {
        xyVec.map( v => v.x * v.x).sum * n
    }
    
    // `d` = the squared sum of all x-values
    val d: Double = {
        val xSum: Double = xyVec.map(_.x).sum
        xSum * xSum
    }
    
    // slope = m = (a - b) / (c - d)
    val m: Double = (a - b) / (c - d)
    
    // Get y-intercept (yInt)
    
    // `e` = the sum of all y-values
    val e: Double = xyVec.map(_.y).sum
    
    // `f` = the slope times the sum of all x-values
    val f: Double = m * xyVec.map(_.x).sum
    
    // y-intercept = (e - f) / n
    val yInt: Double = (e - f) / n
    
    // line-equation
    // y = (m * x) + yInt
    
    xyVec.map( xy => {
        (m * xy.x) + yInt
    })
    
}


nDays: Int = 28
pickFourStates: Vector[String] = Vector(
  "Massachusetts",
  "Florida",
  "South Carolina"
)
defined function toTrendLine


We graph *per capita* death-tolls, total cases, daily cases, and daily deaths for these: 

In [27]:
statesData

res26: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...

In [28]:
val pickFourStatesData: Vector[StatesData] = {
    pickFourStates.map( s => pickAState(s)) :+ statesData
}

val pickFourStatesDataNoNat: Vector[StatesData] = {
    pickFourStates.map( s => pickAState(s))
}

val pickFourCasesTrendline: Unit = {
    val nDays = 28
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        toTrendLine(dailyCases(s,true).takeRight(nDays)) 
    })
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Daily Cases Trendline, ${nDays} days, per ${perCapString}"""
    
    plotData(data, labels, title )
}

/*
val pickFourCasesAbsolute: Unit = {
    
    val data: Vector[Vector[Double]] = pickFourStatesDataNoNat.map( s => {
        mountingCases(s,false)
    })
    
    val labels = pickFourStates
    val title = s"""Mounting Cases (Raw Numbers)"""
    
    plotData(data, labels, title )
}
*/


val pickFourCasesPerCap: Unit = {
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        mountingCases(s,true)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Mounting Cases, per ${perCapString}"""
    
    plotData(data, labels, title )
}


val pickFourDailyCasesPerCap: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data


    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyCases(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Cases, per ${perCapString}, ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}

/*
val pickFourDailyCasesPerCapCentered: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data


    
    val data1: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyCases(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val data = centerCurves(data1)
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Cases, per ${perCapString}, ${rollingAve} day ave. Peaks aligned."""
    
    plotData(data, labels, title )
}
*/



val pickFourActiveCasesPerCap: Unit = {
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        activeCases(s,true)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Active Cases, per ${perCapString}"""
    
    plotData(data, labels, title )
}

val pickFourDailyCasesPerCapNDays: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyCases(s, true).takeRight(nDays).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Cases, last ${nDays} days, per ${perCapString}, ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}


val pickFourDeathsTrendline: Unit = {
    val nDays = 21
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        toTrendLine(dailyDeaths(s,true).takeRight(nDays))
    })
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Daily Deaths Trendline, ${nDays} days, per ${perCapString}"""
    
    plotData(data, labels, title )
}

/*
val pickFourDeathsAbsolute: Unit = {
    
    val data: Vector[Vector[Double]] = pickFourStatesDataNoNat.map( s => {
        mountingDeaths(s,false)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Mounting Deaths"""
    
    plotData(data, labels, title )
}
*/


val pickFourDeathsPerCap: Unit = {
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        mountingDeaths(s,true)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"
    val title = s"""Mounting Deaths, per ${perCapString}"""
    
    plotData(data, labels, title )
}


val pickFourDailyDeathsPerCap: Unit = {
    
    val rollingAve: Int = 14 // change to 1 for raw data

    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyDeaths(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Deaths, per ${perCapString}, ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}

/*
val pickFourDailyDeathsPerCapCentered: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data

    val data1: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyDeaths(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val data = centerCurves(data1)
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Deaths, per ${perCapString}, ${rollingAve} day ave. Peaks aligned."""
    
    plotData(data, labels, title )
}
*/

/*
val pickFourDailyDeathsCentered: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data

    val data1: Vector[Vector[Double]] = pickFourStatesDataNoNat.map( s => {
        dailyDeaths(s, false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val data = centerCurves(data1)
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Deaths, ${rollingAve} day ave. Peaks aligned."""
    
    plotData(data, labels, title )
}
*/


val pickFourDailyDeathsPerCapNDays: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        dailyDeaths(s, true).takeRight(nDays).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Daily Deaths, last ${nDays} days, per ${perCapString}, ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}


pickFourStatesData: Vector[StatesData] = Vector(
  StatesData(
    Vector(
      OneStateData(
        Vector(
          StateDay(
            "2020-01-21",
...
pickFourStatesDataNoNat: Vector[StatesData] = Vector(
  StatesData(
    Vector(
      OneStateData(
        Vector(
          StateDay(
            "2020-01-21",
...

## Evolving CFR

In [29]:
val pickFourDailyDeathsCFR: Unit = {
    
    val rollingAve: Int = 14 // change to 1 for raw data
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        val aveDD: Vector[Double] = mountingDeaths(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        val aveDC: Vector[Double] = mountingCases(s, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        aveDD.zipWithIndex.map( ddi => {
            (ddi._1 / aveDC(ddi._2) ) * 100
        })
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Evolving CFR, as %."""
    
    plotData(data, labels, title )
}

val dropDaysForCFR = 100

val pickFourDailyDeathsCFRMinusInit: Unit = {
    
    val rollingAve: Int = 14 // change to 1 for raw data
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        val aveDD: Vector[Double] = mountingDeaths(s, true).drop(dropDaysForCFR).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        val aveDC: Vector[Double] = mountingCases(s, true).drop(dropDaysForCFR).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        aveDD.zipWithIndex.map( ddi => {
            (ddi._1 / aveDC(ddi._2) ) * 100
        })
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Evolving CFR (Omitting the first 50 days), as %. ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}


val pickFourDailyDeathsCFRMinusInitMulti: Unit = {
    
    val rollingAve: Int = 14 // change to 1 for raw data
    val multiplier: Int = 25
    
    val data: Vector[Vector[Double]] = pickFourStatesData.map( s => {
        val aveDD: Vector[Double] = mountingDeaths(s, true).drop(dropDaysForCFR).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        val aveDC: Vector[Double] = mountingCases(s, true).drop(dropDaysForCFR).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
        aveDD.zipWithIndex.map( ddi => {
            (ddi._1 / (aveDC(ddi._2) * multiplier) ) * 100
        })
    })
    
    val labels = pickFourStates :+ "Natl. Ave"

    val title = s"""Evolving CFR with ${multiplier}x denominator, as %. ${rollingAve} day ave."""
    
    plotData(data, labels, title )
}


dropDaysForCFR: Int = 100

## Comparing Curves for a State

We hear that deaths are a trailing indicator, and so the press reports "new cases" as the meaningful datum in the moment. We are to understand that with more new cases *now*, there will inevitably be a corresponding spike in people dying about two weeks hence. 

We can see if this holds true by comparing one state's daily new-case plot with is daily death plot. We'll want to add a multiplier to the daily death plot to make them comparable in scale. We just want to compare curves.

With the 100x multiplier, the daily deaths look terrifying, so we've added the actual daily deaths in, for honesty. Look at the mostly flat green line at the bottom.

In [30]:
val theState: String = "South Carolina"

val oneStateData: StatesData = pickAState(theState)

val rollingAve: Int = 7 // for smoothing; change to 1 for raw data

val xFactor: Int = 100 // multiply daily deaths by this much, for comparison

val latestCaseCount: Double = 6497.0+ 1652
val latestDeathCount: Double = 10.0+ 0
val flueEpi: Double = (4832000.0/100000.0) * 150

val cumulativeDeathsCompare: Unit = {
    
    val compCountry = "United Kingdom"
    val compDeaths = 2241.0
    
    val compCountry2 = "Sweden"
    val compDeaths2 = 1504.0
    
    val dc: Vector[Double] = {
        mountingDeaths(oneStateData,true)
    }
    
    val cd: Vector[Double] = dc.map(v => {
        compDeaths
    })
    
    val cd2: Vector[Double] = dc.map(v => {
        compDeaths2
    })
    
    val data: Vector[Vector[Double]] = Vector(
        dc, cd, cd2
    )   
    
    val labels = Vector(s"${theState} Deaths", s"${compCountry} deaths as of Day ${maxRecords}.",  s"${compCountry2} deaths as of Day ${maxRecords}." )
    val title = s"""Mounting Deaths per 1,000,000 for ${theState} compared to ${compCountry} and ${compCountry2}."""
    
    
    plotData(data, labels, title )
}

val thisStateCasesOnly: Unit = {
    

    
    val dc: Vector[Double] = {
        dailyCases(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    }
    val currentCases: Vector[Double] = {
        dc.map( n => latestCaseCount)
    }
    
    val fluEpiCases: Vector[Double] = {
        dc.map( n => flueEpi)
    }
    
    val data: Vector[Vector[Double]] = Vector(
        dc, currentCases
        
    )
    
    val labels = Vector(s"Cases", "Latest Count" )
    val title = s"""Daily Cases for ${theState}, ${rollingAve}-day ave."""
    
    plotData(data, labels, title )
}

val thisStateCasesOnly28: Unit = {
    
    val days: Int = 28
    
    val dc: Vector[Double] = {
        dailyCases(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve).takeRight(days)
    }
    val currentCases: Vector[Double] = {
        dc.map( n => latestCaseCount).takeRight(days)
    }
    
    val fluEpiCases: Vector[Double] = {
        dc.map( n => flueEpi).takeRight(days)
    }
    
    val data: Vector[Vector[Double]] = Vector(
        dc, currentCases
        
    )
    
    val labels = Vector(s"Cases", "Latest Count" )
    val title = s"""Daily Cases for ${theState}, last ${days} days, ${rollingAve}-day ave."""
    
    plotData(data, labels, title )
}


val thisStateDeathsOnly: Unit = {
    
    val dd1: Vector[Double] = {
       dailyDeaths(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve) 
    }
    
    val dd2: Vector[Double] = {
        dailyDeaths(oneStateData,false).sliding(rollingAve * 3,1).toVector.map(_.sum / (rollingAve * 3))
    }
    
 
    
    val data1: Vector[Vector[Double]] = Vector(
        dd1, dd2
        
    )
    
    val data2 = centerCurves(data1)
    
    val cd: Vector[Double] = {
        data2.head.map( n => latestDeathCount)
    }
    
    val data3: Vector[Vector[Double]] = data2 ++ Vector(cd)
    
    
    val labels = Vector(s"Deaths (${rollingAve}-day ave.)", s"Deaths (${rollingAve * 3}-day ave.)", "Latest Daily" )
    val title = s"""Daily Deaths for ${theState}"""
    
    plotData(data3, labels, title )
}

val thisStateDeathsOnly2: Unit = {
    
    val dd1: Vector[Double] = {
       dailyDeaths(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve) 
    }
    
    val dd2: Vector[Double] = {
        val realData = dailyDeaths(oneStateData,false).sliding(rollingAve * 3,1).toVector.map(_.sum / (rollingAve * 3))
        val paddingLeft = (1 to rollingAve * 2).map( d => 0.0).toVector
        paddingLeft ++ realData
    }
    
 
    
    val data1: Vector[Vector[Double]] = Vector(
        dd1, dd2
        
    )
    
    val data2 = centerCurves(data1)
    
    val cd: Vector[Double] = {
        data1.head.map( n => latestDeathCount)
    }
    
    val data3: Vector[Vector[Double]] = data1 ++ Vector(cd)
    
    
    val labels = Vector(s"Deaths (${rollingAve}-day ave.)", s"Deaths (${rollingAve * 3}-day ave.)", "Latest Daily" )
    val title = s"""Daily Deaths for ${theState}"""
    
    plotData(data3, labels, title )
}

val thisStateDeathsOnly28: Unit = {
    
    var howMany = 28
    
    val dd1: Vector[Double] = {
       dailyDeaths(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve).takeRight(howMany)
    }
    
    val dd2: Vector[Double] = {
        val realData = dailyDeaths(oneStateData,false).sliding(rollingAve * 3,1).toVector.map(_.sum / (rollingAve * 3)).takeRight(howMany)
        realData
    }
    
 
    
    val data1: Vector[Vector[Double]] = Vector(
        dd1, dd2
        
    )
    
    val data2 = centerCurves(data1)
    
    val cd: Vector[Double] = {
        data1.head.map( n => latestDeathCount)
    }
    
    val data3: Vector[Vector[Double]] = data1 ++ Vector(cd)
    
    
    val labels = Vector(s"Deaths (${rollingAve}-day ave.)", s"Deaths (${rollingAve * 3}-day ave.)", "Latest Daily" )
    val title = s"""Daily Deaths for ${theState}, last ${howMany} days."""
    
    plotData(data3, labels, title )
}

val pickFourCasesAbs: Unit = {
    
    val data: Vector[Vector[Double]] = Vector(
        dailyDeaths(oneStateData,false).map(_ * xFactor).sliding(rollingAve,1).toVector.map(_.sum / rollingAve),
        dailyCases(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve),
        dailyDeaths(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)


    )
    
    val labels = Vector(s"Daily Deaths (x${xFactor})", "Daily Cases", "Daily Deaths (actual)" )
    val title = s"""Daily cases and deaths (x${xFactor}), ${rollingAve}-day ave., ${theState}"""
    
    plotData(data, labels, title )
}

val scCancer: Vector[Double] = {
    val pop = 5150000.0
    val deaths = 10356.0
    val pc: Double = deaths / 365
    (1 to dailyDeaths(oneStateData,true).map(_ * xFactor).sliding(rollingAve,1).size).toVector.map( d => pc )
}

val scAccidents: Vector[Double] = {
    val pop = 5150000.0
    val deaths = 3147.0
    val pc: Double = deaths / 365
    (1 to dailyDeaths(oneStateData,true).map(_ * xFactor).sliding(rollingAve,1).size).toVector.map( d => pc )
}

val scAll: Vector[Double] = {
    val pop = 5150000.0
    val deaths = 49441.0
    val pc: Double = deaths / 365
    (1 to dailyDeaths(oneStateData,true).map(_ * xFactor).sliding(rollingAve,1).size).toVector.map( d => pc )
}

val scHeart: Vector[Double] = {
    val pop = 5150000.0
    val deaths = 10418.0
    val pc: Double = deaths / 365
    (1 to dailyDeaths(oneStateData,true).map(_ * xFactor).sliding(rollingAve,1).size).toVector.map( d => pc )
}

val scCLRD: Vector[Double] = {
    val pop = 5150000.0
    val deaths = 2983.0
    val pc: Double = deaths / 365
    (1 to dailyDeaths(oneStateData,true).map(_ * xFactor).sliding(rollingAve,1).size).toVector.map( d => pc )
}

val pickFourCasesPerCap: Unit = {
        
    val data: Vector[Vector[Double]] = Vector(
        dailyDeaths(oneStateData,false).sliding(rollingAve,1).toVector.map(_.sum / rollingAve),
        scCancer,
        scAccidents,
        scHeart,
        scCLRD
    )
    

    
    val labels = Vector(s"Daily Covid Deaths", s"SC Daily Cancer Deaths", s"SC Daily Accident Deaths", "SC Daily Deaths, Heart", "SC Daily Deaths, Resp."  )
    val title = s"""Compared to 2018, ${rollingAve}-day ave., ${theState}"""
    
    plotData(data, labels, title )
}

val cumulativeDeathsCompare2: Unit = {


    val dc: Vector[Double] = {
        mountingDeaths(oneStateData,false)
    }
    
    val mountingAllDeaths: Vector[Double] = {
        val pop = 5150000.0
        val deaths = 50633.0
        val pc: Double = deaths / 365
        val flat: Vector[Double] = dc.map( d => pc)
        val indexedFlat: Vector[(Double, Int)] = flat.zipWithIndex
        indexedFlat.map( mv => {
            val i: Int = mv._2
            val shortVec = flat.take(i + 1)
            val sumVec: Double = shortVec.sum
            sumVec
        })
    }

    val mountingAccidents: Vector[Double] = {
        val pop = 5150000.0
        val deaths = 3147.0
        val pc: Double = deaths / 365
        val flat: Vector[Double] = dc.map( d => pc)
        val indexedFlat: Vector[(Double, Int)] = flat.zipWithIndex
        indexedFlat.map( mv => {
            val i: Int = mv._2
            val shortVec = flat.take(i + 1)
            val sumVec: Double = shortVec.sum
            sumVec
        })
    }

    val mountingCancer: Vector[Double] = {
        val pop = 5150000.0
        val deaths = 10356.0
        val pc: Double = deaths / 365
         val flat: Vector[Double] = dc.map( d => pc)
        val indexedFlat: Vector[(Double, Int)] = flat.zipWithIndex
        indexedFlat.map( mv => {
            val i: Int = mv._2
            val shortVec = flat.take(i + 1)
            val sumVec: Double = shortVec.sum
            sumVec
        })
    }
    
       val mountingResp: Vector[Double] = {
        val pop = 5150000.0
        val deaths = 2990.0
        val pc: Double = deaths / 365
         val flat: Vector[Double] = dc.map( d => pc)
        val indexedFlat: Vector[(Double, Int)] = flat.zipWithIndex
        indexedFlat.map( mv => {
            val i: Int = mv._2
            val shortVec = flat.take(i + 1)
            val sumVec: Double = shortVec.sum
            sumVec
        })
    }

    val data: Vector[Vector[Double]] = Vector(
        dc, mountingAccidents, mountingCancer, mountingResp, mountingAllDeaths
    )   

    val labels = Vector(s"${theState} Covid Deaths", s"Accidental Deaths.",  s"Cancer Deaths.", "CLRD Deaths.", "All Deaths (2018)" )
    val title = s"""Mounting Deaths per 1,000,000 for ${theState}: Covid vs. (2018) All Deaths,  Accidents, Cancer, and Chronic Resp."""


    plotData(data, labels, title )
}





theState: String = "South Carolina"
oneStateData: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay(
          "2020-01-21",
          "South Carolina",
...
rollingAve: Int = 7
xFactor: Int = 100
latestCaseCount: Double = 8149.0
latestDeathCount: Double = 10.0
flueEpi: Double = 7248.0
scCancer: Vector[Double] = Vector(
  28.372602739726027,
  28.372602739726027,
  28.372602739726027,
  28.372602739726027,
  28.372602739726027,
  28.372602739726027,
...
scAccidents: Vector[Double] = Vector(
  8.621917808219179,
  8.621917808219179,
  8.621917808219179,
  8.621917808219179,
  8.621917808219179,
  8.621917808219179,
...
scAll: Vector[Double] = Vector(
  135.45479452054795,
  135.45479452054795,
  135.45479452054795,
  135.45479452054795,
  135.45479452054795,
  135.45479452054795,
...
scHeart: Vector[Double] = Vector(
  28.542465753424658,
  28.542465753424658,
  28.542465753424658,
  28.542465753424658,
  28.542465753424658,
  28.542465753424658,
...
scC

## Evolving Trendlines

In [31]:
def getShadedScatterVec( data: Vector[Vector[Double]], lables: Vector[String], color: Option[(Int, Int, Int, Double)] = None): Vector[Scatter] = {
    data.zipWithIndex.map( vi => {
        
        
        val colorList: Vector[(Int, Int, Int, Double)] = {
            val shades: Vector[Double] = {
                val step: Double = 1.0 / data.size
                (1 to data.size).toVector.map( n => {
                    (n * step)
                })
            }
            val notLast = shades.dropRight(1).map( s => {
                val tone: Int = (240 - (s * (1.0 / data.size))).toInt
                (240,0,0,s)
            })
            val last = Vector((0,0,0,1.0))
            notLast ++ last
        }
        
        val index = vi._2
        val dataVec = vi._1
        val label = lables(index)
        val thisColor = {
            color match {
                case Some(tp) => tp
                case None => colorList( index % colorList.size )
            }
        }
    
        Scatter(
          (1 to dataVec.size),
          dataVec,
          name = label,
          mode = ScatterMode(ScatterMode.Lines),
          marker = Marker(
            color = Color.RGBA(
            thisColor._1,
            thisColor._2,
            thisColor._3,
            thisColor._4
           ),
          )
        )    
    })
}

def plotShadedData( data: Vector[Vector[Double]], labels: Vector[String], title: String ): Unit = {
    
    val dataNew = getShadedScatterVec( data, labels)
    val layoutNew = Layout(title)

    plot(dataNew, layoutNew)
}




val nDays: Int = 28 // How long to measure the trendline

val howOften: Int = 1 // Get a trend line each `howOften` days

val howMany: Int = 35 // Compare `howMany` trendlines

val evCases: Vector[Vector[Double]] = dailyCases(oneStateData,false).sliding(nDays, howOften).toVector.takeRight(howMany)
val evDeaths: Vector[Vector[Double]] = dailyDeaths(oneStateData,false).sliding(nDays, howOften).toVector.takeRight(howMany)

val caseTrends: Vector[Vector[Double]] = evCases.map( c => {
    toTrendLine(c)
})

val deathTrends: Vector[Vector[Double]] = evDeaths.map( c => {
    toTrendLine(c)
})

val labels =  (1 to howMany).toVector.map(_.toString)

val title =  "Cases Trendlines"

plotShadedData(caseTrends, labels, s"Cases Trendlines for ${theState}, ${nDays} days" )

plotShadedData(deathTrends, labels, s"Deaths Trendlines ${theState}, ${nDays} days" )




defined function getShadedScatterVec
defined function plotShadedData
nDays: Int = 28
howOften: Int = 1
howMany: Int = 35
evCases: Vector[Vector[Double]] = Vector(
  Vector(
    493.0,
    0.0,
    1763.0,
    0.0,
    0.0,
...
evDeaths: Vector[Vector[Double]] = Vector(
  Vector(
    25.0,
    0.0,
    60.0,
    0.0,
    0.0,
...
caseTrends: Vector[Vector[Double]] = Vector(
  Vector(
    500.35714285714283,
    518.6904761904761,
    537.0238095238095,
    555.3571428571429,
    573.6904761904761,
...
deathTrends: Vector[Vector[Double]] = Vector(
  Vector(
    19.15270935960591,
    18.845101258894363,
    18.537493158182812,
    18.229885057471265,
    17.922276956759717,
...
labels: Vector[String] = Vector(
  "1",
  "2",
  "3",
  "4",
  "5",
  "6",
...
title: String = "Cases Trendlines"

## Comparing one State to the Average

We might want to see one state's statistics compared to the national average.

In [32]:
val theStateToCompare: String = "South Carolina"

val oneStateDataToCompare: StatesData = pickAState(theStateToCompare)

val allOtherStates: StatesData = {
    val states: Vector[OneStateData] = statesData.states.filter(_.days.head.state != theStateToCompare)
    StatesData(states)
}

val compareCasesPerCap: Unit = {
    val data: Vector[Vector[Double]] = Vector(
        mountingCases(oneStateDataToCompare, true), mountingCases(allOtherStates, true)
    )
    val labels = Vector(theStateToCompare, "National")
    val title = s"Mounting Cases, ${theStateToCompare} vs. Natl. Ave., per ${perCapString}"
    
    plotData(data, labels, title )
}

val compareActiveCasesPerCap: Unit = {
    val data: Vector[Vector[Double]] = Vector(
        activeCases(oneStateDataToCompare, true), activeCases(allOtherStates, true)
    )
    val labels = Vector(theStateToCompare, "National")
    val title = s"Active Cases, ${theStateToCompare} vs. Natl. Ave., per ${perCapString}"
    
    plotData(data, labels, title )
}

val compareDeathsPerCap: Unit = {
    val data: Vector[Vector[Double]] = Vector(
        mountingDeaths(oneStateDataToCompare, true), mountingDeaths(allOtherStates, true)
    )
    val labels = Vector(theStateToCompare, "National")
    val title = s"Mounting Deaths, ${theStateToCompare} vs. Natl. Ave., per ${perCapString}"
    
    plotData(data, labels, title )
}

val compareDailyCasesPerCap: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data

    val data: Vector[Vector[Double]] = Vector(
        dailyCases(oneStateDataToCompare, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve), 
        dailyCases(allOtherStates, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    )
    val labels = Vector(theStateToCompare, "National")
    val title = s"Daily Cases, ${theStateToCompare} vs. Natl. Ave., per ${perCapString}, ${rollingAve} day ave."
    
    plotData(data, labels, title )
}

val compareDailyDeathsPerCap: Unit = {
    
    val rollingAve: Int = 7 // change to 1 for raw data

    val data: Vector[Vector[Double]] = Vector(
        dailyDeaths(oneStateDataToCompare, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve), 
        dailyDeaths(allOtherStates, true).sliding(rollingAve,1).toVector.map(_.sum / rollingAve)
    )
    val labels = Vector(theStateToCompare, "National Ave.")
    val title = s"Daily Deaths, ${theStateToCompare} vs. Natl. Ave., per ${perCapString}, ${rollingAve} day ave."
    
    plotData(data, labels, title )
}



theStateToCompare: String = "South Carolina"
oneStateDataToCompare: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay(
          "2020-01-21",
          "South Carolina",
...
allOtherStates: StatesData = StatesData(
  Vector(
    OneStateData(
      Vector(
        StateDay("2020-01-21", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-22", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
        StateDay("2020-01-23", "Alabama", 4903185, true, 0, 0, 0, 0, 0, 0),
...

## Where Are Cases Rising?

For reference:

~~~ scala
case class StateDay(
    date: String,
    state: String,
    population: Int,
    isRedState: Boolean,
    newDeaths: Int,
    newCases: Int,
    totalDeaths: Int,
    totalCases: Int,
    activeCases: Int,
    lockdown: Int
)

case class OneStateData( days: Vector[StateDay]) 

case class StatesData( states: Vector[OneStateData] )
~~~


In [33]:
val spanOfDays: Int = 29


val newCasesComp: Vector[(String, Vector[Double])] = {
    statesData.states.map( sd => {
        val st: String = sd.days.last.state
        val cases: Vector[Double] = dailyCases(StatesData(Vector(sd)), true).takeRight(spanOfDays)
        (st, cases)
    })
}

val newCasesTrend: Vector[(String, Vector[Double], Double)] = {
    newCasesComp.map( ncc => {
        val s: String = ncc._1
        val v: Vector[Double] = toTrendLine(ncc._2)
        val d: Double = v.last - v.head
        (s, v, d)
    }).sortBy( m => m._3 )
}

val newDeathsComp: Vector[(String, Vector[Double])] = {
    statesData.states.map( sd => {
        val st: String = sd.days.last.state
        val cases: Vector[Double] = dailyDeaths(StatesData(Vector(sd)), true).takeRight(spanOfDays)
        (st, cases)
    })
}

val newDeathsTrend: Vector[(String, Vector[Double], Double)] = {
    newDeathsComp.map( ncc => {
        val s: String = ncc._1
        val v: Vector[Double] = toTrendLine(ncc._2)
        val d: Double = v.last - v.head
        (s, v, d)
    }).sortBy( m => m._3 )
}


spanOfDays: Int = 29
newCasesComp: Vector[(String, Vector[Double])] = Vector(
  (
    "Alabama",
    Vector(
      59.9610253335332,
      337.53570383332465,
      131.9550455469251,
...
newCasesTrend: Vector[(String, Vector[Double], Double)] = Vector(
  (
    "Maine",
    Vector(
      695.3234080379555,
      688.4957405924073,
      681.6680731468591,
...
newDeathsComp: Vector[(String, Vector[Double])] = Vector(
  (
    "Alabama",
    Vector(
      0.0,
      4.078981315206341,
      3.8750322494460234,
...
newDeathsTrend: Vector[(String, Vector[Double], Double)] = Vector(
  (
    "Tennessee",
    Vector(
      27.15833064397558,
      26.401075290483554,
      25.643819936991527,
...

In [34]:
val worstTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newCasesTrend.map( nct => {
        nct._2
    }).takeRight(howMany).reverse
    
    
    val labels: Vector[String] = newCasesTrend.map(_._1).takeRight(howMany).reverse
    val title = s"""${howMany} States with Cases Rising Most, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}



val bestTrendline: Unit = {
    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newCasesTrend.map( nct => {
        nct._2
    }).take(howMany).reverse
    
    
    val labels: Vector[String] = newCasesTrend.map(_._1).take(howMany).reverse
    val title = s"""${howMany} States with Cases Rising Least, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

val risingTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newCasesTrend.filter(_._3 > 0).map( nct => {
        nct._2
    }).reverse
    
    
    val labels: Vector[String] = newCasesTrend.filter(_._3 > 0).map( nct => {
        nct._1
    }).reverse
    val title = s"""${data.size} States have Cases Rising, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

val fallingTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newCasesTrend.filter(_._3 <= 0).map( nct => {
        nct._2
    }).reverse
    
    
    val labels: Vector[String] = newCasesTrend.filter(_._3 <= 0).map( nct => {
        nct._1
    }).reverse
    val title = s"""${data.size} States have Cases Falling, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

In [35]:
val worstDeathTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newDeathsTrend.map( nct => {
        nct._2
    }).takeRight(howMany).reverse
    
    
    val labels: Vector[String] = newDeathsTrend.map(_._1).takeRight(howMany).reverse
    val title = s"""${howMany} States with Deaths Rising Most, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}



val bestDeathTrendline: Unit = {
    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newDeathsTrend.map( nct => {
        nct._2
    }).take(howMany).reverse
    
    
    val labels: Vector[String] = newDeathsTrend.map(_._1).take(howMany).reverse
    val title = s"""${howMany} States with Deaths Rising Least, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

val risingDeathTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newDeathsTrend.filter(_._3 > 0).map( nct => {
        nct._2
    }).reverse
    
    
    val labels: Vector[String] = newDeathsTrend.filter(_._3 > 0).map( nct => {
        nct._1
    }).reverse
    val title = s"""${data.size} States have Deaths Rising, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

val fallingDeaethTrendline: Unit = {

    
    val howMany: Int = 17
    
    val data: Vector[Vector[Double]] = newDeathsTrend.filter(_._3 <= 0).map( nct => {
        nct._2
    }).reverse
    
    
    val labels: Vector[String] = newDeathsTrend.filter(_._3 <= 0).map( nct => {
        nct._1
    }).reverse
    val title = s"""${data.size} States have Deaths Falling, over the last ${spanOfDays} days"""
    
    plotData(data, labels, title )
}

## 